# Casos positivos de Covid-19 por províncias em Itália #

## Ligação ao QGIS ##

In [1]:
import os
import sys
from osgeo import ogr
os.environ['QT_QPA_PLATFORM'] = 'offscreen'
sys.path.insert(0,'/usr/local/share/qgis/python')
from qgis.core import *
QgsApplication.setPrefixPath("/usr/local", True) 
from qgis.gui import *
from qgis import processing
from IPython.display import Image
from qgis.PyQt.QtGui import QColor, QImage
from qgis.PyQt.QtCore import QSize, QBuffer, QIODevice
from qgis.utils import iface
from qgis.core import *
from qgis.PyQt.QtGui import *
from qgis.PyQt.QtCore import *

qgs = QgsApplication([], True)
qgs.initQgis()
print(QgsApplication.showSettings())
project = QgsProject.instance()

Application state:
QGIS_PREFIX_PATH env var:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS
Prefix:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS
Plugin Path:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../PlugIns/qgis
Package Data Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources
Active Theme Name:	
Active Theme Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/resources/themes//icons/
Default Theme Path:	:/images/themes/default/
SVG Search Paths:	/usr/local/../Resources/svg/
		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/svg/
		/Users/dianamartins/Library/Application Support/profiles/default/svg/
User DB Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/resources/qgis.db
Auth DB Path:	/Users/dianamartins/Library/Application Support/profiles/default/qgis-auth.db



### Carregamento da shapefile que define as províncias de Itália ###

In [2]:
italy_map = "/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/ITA_adm/ITA_adm2.shp"
vlayer = QgsVectorLayer(italy_map, "italy_map", "ogr")
if not vlayer.isValid():
    print("Layer failed to load!")
else:
    QgsProject.instance().addMapLayer(vlayer)
    print("Layer loaded!")

Layer loaded!


### Carregamento do ficheiro csv que contém o número de casos de covid-19 por província ###

In [3]:
csv_path = "file:///Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/casos_italia_provincias.csv?delimiter=;"
csv_layer = QgsVectorLayer(csv_path, 'Data', 'delimitedtext')

if not csv_layer.isValid():
    print('Layer failed to load!')
else:
    QgsProject.instance().addMapLayer(csv_layer)
    print("Layer loaded !")

Layer loaded !


### Junção da shapefile com o ficheiro csv ###

In [4]:
joinName='denominazione_provincia'
targetName='NAME_2'

joinObject=QgsVectorLayerJoinInfo()
joinObject.setJoinFieldName(joinName)
joinObject.setTargetFieldName(targetName)
joinObject.setJoinLayerId(csv_layer.id())
joinObject.setUsingMemoryCache(True)
joinObject.setJoinLayer(csv_layer)
flag = vlayer.addJoin(joinObject)

In [6]:
nomesprovincias_layer = vlayer.clone()
nomesprovincias_layer.setName("Províncias de Itália")

for field in nomesprovincias_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column ID_2 Load
Column NAME_2 Load
Column TYPE_2 Load
Column ENGTYPE_2 Load
Column NL_NAME_2 Load
Column VARNAME_2 Load
Column Data_data Load
Column Data_stato Load
Column Data_codice_regione Load
Column Data_denominazione_regione Load
Column Data_codice_provincia Load
Column Data_sigla_provincia Load
Column Data_lat Load
Column Data_long Load
Column Data_totale_casi Load
Column Data_note_it Load
Column Data_note_en Load


### Mapa das províncias de Itália ###

In [7]:
label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_2"

text_format = QgsTextFormat()
text_format.setFont(QFont("Arial", 10))
text_format.setSize(30) 

background_color = QgsTextBackgroundSettings()
background_color.setEnabled(False)

text_format.setBackground(background_color )
label_settings.setFormat(text_format)

nomesprovincias_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
nomesprovincias_layer.setLabelsEnabled(True)
nomesprovincias_layer.triggerRepaint()

In [8]:
xt = nomesprovincias_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

project = QgsProject().instance()
project.addMapLayers([nomesprovincias_layer])
manager = project.layoutManager()
layoutName = 'provincias'
layouts_list = manager.printLayouts()
for layout in layouts_list:
    if layout.name() == layoutName:
        manager.removeLayout(layout)
        
layout = QgsPrintLayout(project)
layout.initializeDefaults()
layout.setName(layoutName)
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))


map = QgsLayoutItemMap(layout)
map.setRect(20,20,20,20)
map.setLayers([nomesprovincias_layer])

ms = QgsMapSettings()
ms.setLayers([nomesprovincias_layer])
ms.setExtent(xt)
map.setExtent(xt)

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map.setBackgroundColor(QColor(230, 234, 238))

legend = QgsLayoutItemLegend(layout)
legend.setReferencePoint(6)
legend.setScale(3)
legend.attemptMove(QgsLayoutPoint(0,height,QgsUnitTypes.LayoutMillimeters))

layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.setLinkedMap(map)

exporter = QgsLayoutExporter(manager.layoutByName("provincias"))

image = exporter.renderPageToImage(0)
image = exporter.renderPageToImage(0)

from IPython.display import Image
imgbuf= QBuffer()
imgbuf.open( QIODevice.ReadWrite )
image.save( imgbuf,"PNG" )
image.save('/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Imagens/provincias_italia',"PNG")
Image( imgbuf.data() )

## Mapa com o total de casos positivos por província ##

In [9]:
provincias_layer = vlayer.clone()
provincias_layer.setName("Total de casos positivos nas províncias de Itália")

for field in provincias_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column ID_2 Load
Column NAME_2 Load
Column TYPE_2 Load
Column ENGTYPE_2 Load
Column NL_NAME_2 Load
Column VARNAME_2 Load
Column Data_data Load
Column Data_stato Load
Column Data_codice_regione Load
Column Data_denominazione_regione Load
Column Data_codice_provincia Load
Column Data_sigla_provincia Load
Column Data_lat Load
Column Data_long Load
Column Data_totale_casi Load
Column Data_note_it Load
Column Data_note_en Load


In [10]:
label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_2"

text_format = QgsTextFormat()
text_format.setFont(QFont("Arial", 10))
text_format.setSize(30) 

background_color = QgsTextBackgroundSettings()
background_color.setEnabled(False)

text_format.setBackground(background_color )
label_settings.setFormat(text_format)

nomesprovincias_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
nomesprovincias_layer.setLabelsEnabled(True)
nomesprovincias_layer.triggerRepaint()

In [11]:
from qgis.PyQt import QtGui

myOpacity = 1
myTargetField = 'Data_totale_casi'
myRangeList = []

myMin = 0
myMax = 0
myLabel = '0-0'
myColour = QtGui.QColor('#ffffff')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 0
myMax = 400
myLabel = '0 - 400'
myColour = QtGui.QColor('#e68a00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 400
myMax = 800
myLabel = '400 - 800'
myColour = QtGui.QColor('#cc7a00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 800
myMax = 1200
myLabel = '800 - 1200'
myColour = QtGui.QColor('#b36b00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 1200
myMax = 2000
myLabel = '1200 - 2000'
myColour = QtGui.QColor('#995c00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 2000
myMax = 5000
myLabel = '2000 - 5000'
myColour = QtGui.QColor('#804d00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 5000
myMax = 10000
myLabel = '5000 - 10000'
myColour = QtGui.QColor('#663d00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 10000
myMax = 15000
myLabel = '10000 - 15000'
myColour = QtGui.QColor('#4d2e00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 15000
myMax = 20000
myLabel = '15000 - 20000'
myColour = QtGui.QColor('#331f00')
mySymbol = QgsSymbol.defaultSymbol(provincias_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)


myRenderer = QgsGraduatedSymbolRenderer('', myRangeList)
myClassificationMethod = QgsApplication.classificationMethodRegistry().method("EqualInterval")
myRenderer.setClassificationMethod(myClassificationMethod)
myRenderer.setClassAttribute(myTargetField)

provincias_layer.setRenderer(myRenderer)

In [ ]:
xt = provincias_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

project = QgsProject().instance()
project.addMapLayers([provincias_layer])
manager = project.layoutManager()
layoutName = 'Total de casos positivos'
layouts_list = manager.printLayouts()
for layout in layouts_list:
    if layout.name() == layoutName:
        manager.removeLayout(layout)
        
layout = QgsPrintLayout(project)
layout.initializeDefaults()
layout.setName(layoutName)
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))


map = QgsLayoutItemMap(layout)
map.setRect(20,20,20,20)
map.setLayers([provincias_layer])

ms = QgsMapSettings()
ms.setLayers([provincias_layer])
ms.setExtent(xt)
map.setExtent(xt)

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map.setBackgroundColor(QColor(230, 234, 238))

legend = QgsLayoutItemLegend(layout)
legend.setReferencePoint(6)
legend.setScale(3)
legend.attemptMove(QgsLayoutPoint(0,height,QgsUnitTypes.LayoutMillimeters))

layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.setLinkedMap(map)

exporter = QgsLayoutExporter(manager.layoutByName("Total de casos positivos"))

image = exporter.renderPageToImage(0)
image = exporter.renderPageToImage(0)

from IPython.display import Image
imgbuf= QBuffer()
imgbuf.open( QIODevice.ReadWrite )
image.save( imgbuf,"PNG" )
image.save('/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Imagens/casos_provincias',"PNG")
Image( imgbuf.data() )